In [2]:
import sqlite3
import os
import pandas as pd

# 预测价格数据
# dbfilename = os.path.join(r'D:\code\PriceForecast\yuanyoudataset','jbsh_yuanyou.db')
# conn = sqlite3.connect(dbfilename)
# query = 'SELECT * FROM accuracy'
# df1 = pd.read_sql_query(query, conn)
# df1['ds'] =  df1['PREDICT_DATE']
# conn.close()
# print(df1.shape)

# 预测价格数据
dfcsvfilename = os.path.join(r'D:\code\PriceForecast\yuanyoudataset','accuracy_ten.csv')
df1 = pd.read_csv(dfcsvfilename)
print(df1.shape)

# 最高最低价
xlsfilename = os.path.join(r'D:\code\PriceForecast\yuanyoudataset','数据项下载.xls')
df2 = pd.read_excel(xlsfilename)[5:]
df2 = df2.rename(columns = {'数据项名称':'ds','布伦特最低价':'LOW_PRICE','布伦特最高价':'HIGH_PRICE'})
print(df2.shape)



df = pd.merge(df1,df2,on=['ds'],how='left')

df['ds'] =  pd.to_datetime(df['ds'])
# df['PREDICT_DATE'] =  pd.to_datetime(df['PREDICT_DATE'])
df = df.reindex()

print(df.shape)

df.to_csv(os.path.join(r'D:\code\PriceForecast\yuanyoudataset','123.csv'))
# df = df[['ds','min_within_quantile','max_within_quantile']]



# 打印数据框的前几行
print(df.head())
print(df.tail())


(85, 28)
(20, 4)
(85, 31)
          ds      NHITS   Informer       LSTM  iTransformer   TSMixer  \
0 2024-11-25  75.714300  75.523370  73.614220      75.27068  75.03936   
1 2024-11-26  76.039635  75.558270  73.692310      75.04110  74.60100   
2 2024-11-27  77.375790  75.361885  73.826140      74.99121  74.37731   
3 2024-11-28  78.872400  76.339920  73.883484      75.79425  74.04826   
4 2024-11-29  79.576970  76.333170  73.876396      75.89008  74.07330   

    TSMixerx  PatchTST        RNN        GRU  ...          y  \
0  74.581190  75.70277  74.721280  74.512060  ...  73.010002   
1  73.496025  75.97611  74.588060  74.713425  ...  72.809998   
2  73.522026  76.48628  74.486400  74.946010  ...  72.830002   
3  73.416306  76.38267  75.195710  74.946014  ...  73.279999   
4  73.521570  76.20661  75.089966  74.935165  ...  72.940002   

   min_within_quantile  max_within_quantile  id  CREAT_DATE  min_price  \
0             74.41491             75.29100   1  2024-11-22  74.414910   
1 

In [3]:
# 定义一个函数来计算准确率
def calculate_accuracy(row):
    if row['HIGH_PRICE_y'] > row['MIN_PRICE']:
        sorted_prices = sorted([row['LOW_PRICE_y'], row['MIN_PRICE'], row['MAX_PRICE'], row['HIGH_PRICE_y']])
        middle_diff = sorted_prices[2] - sorted_prices[1]
        price_range = row['HIGH_PRICE_y'] - row['LOW_PRICE_y']
        accuracy = middle_diff / price_range
        return accuracy
    else:
        return 0

# 使用 apply 函数来应用计算准确率的函数

columns = ['HIGH_PRICE_y','LOW_PRICE_y','MIN_PRICE','MAX_PRICE']
df[columns] = df[columns].astype(float)
df['ACCURACY'] = df.apply(calculate_accuracy, axis=1)


# 打印结果
print(df[['ds','ACCURACY',]+columns])

df = df[['ds','ACCURACY','PREDICT_DATE','CREAT_DATE']+columns]

KeyError: "None of [Index(['HIGH_PRICE_y', 'LOW_PRICE_y', 'MIN_PRICE', 'MAX_PRICE'], dtype='object')] are in the [columns]"

In [138]:
import datetime
# ds 按周取
df['Ds_Week'] = df['ds'].apply(lambda x: x.strftime('%U'))
df['Pre_Week'] = df['PREDICT_DATE'].apply(lambda x: x.strftime('%U'))

In [139]:
df

ds  ACCURACY PREDICT_DATE  CREAT_DATE  HIGH_PRICE_y  LOW_PRICE_y  \
0  2024-11-26  1.000000   2024-11-26  2024-11-25         73.80        71.63   
1  2024-11-27  1.000000   2024-11-27  2024-11-25         72.85        71.71   
2  2024-11-28  0.789324   2024-11-28  2024-11-25         72.96        71.85   
3  2024-11-29  1.000000   2024-11-29  2024-11-25         73.34        71.75   
4  2024-12-02  0.853412   2024-12-02  2024-11-25         72.89        71.52   
..        ...       ...          ...         ...           ...          ...   
70 2024-11-25  0.118328   2024-11-25  2024-11-22         74.83        72.30   
71 2024-11-26  0.000000   2024-11-26  2024-11-22         73.80        71.63   
72 2024-11-27  0.000000   2024-11-27  2024-11-22         72.85        71.71   
73 2024-11-28  0.000000   2024-11-28  2024-11-22         72.96        71.85   
74 2024-11-29  0.000000   2024-11-29  2024-11-22         73.34        71.75   

    MIN_PRICE  MAX_PRICE Ds_Week Pre_Week  
0   71.071556  76.006900      47       47  
1   71.003624  75.580560      47       47  
2   72.083850  76.204260      47       47  
3   71.329730  75.703950      47       47  
4   71.720825  76.264275      48       48  
..        ...        ...     ...      ...  
70  74.530630  76.673140      47       47  
71  74.440430  76.874565      47       47  
72  74.663180  76.734130      47       47  
73  74.708410  77.141050      47       47  
74  74.703210  77.746170      47       47  

[75 rows x 10 columns]

In [140]:
# 取结束日期上一周的日期
endtime = '2024-12-3'
endtimeweek = datetime.datetime.strptime(endtime, '%Y-%m-%d')
up_week = endtimeweek - datetime.timedelta(days=endtimeweek.weekday() + 14)
up_week_dates = [up_week + datetime.timedelta(days=i) for i in range(14)][4:-2]
up_week_dates = [date.strftime('%Y-%m-%d') for date in up_week_dates]
print(up_week_dates)


df3 = df.copy()
df3 = df3[df3['CREAT_DATE'].isin(up_week_dates)]
df3 = df3[df3['PREDICT_DATE'].isin(up_week_dates)]
print(df3.shape)
df3.to_csv('up_week_dates.csv',index=False)

['2024-11-22', '2024-11-23', '2024-11-24', '2024-11-25', '2024-11-26', '2024-11-27', '2024-11-28', '2024-11-29']


(15, 10)


In [141]:
total = len(df3)
accuracy_rote = 0
# for i,group in df3.groupby('CREAT_DATE'):
for i,group in df3.groupby('ds'):
    print(i)
    print('权重：',round(len(group)/total,2))
    print('准确率：',group['ACCURACY'].sum()/(len(group)/total))
    accuracy_rote += group['ACCURACY'].sum()/(len(group)/total)

print(accuracy_rote)

2024-11-25 00:00:00
权重： 0.07
准确率： 1.7749209486165771
2024-11-26 00:00:00
权重： 0.13
准确率： 7.5
2024-11-27 00:00:00
权重： 0.2
准确率： 8.034364035087705
2024-11-28 00:00:00
权重： 0.27
准确率： 9.718006756756724
2024-11-29 00:00:00
权重： 0.33
准确率： 10.824716981132076
37.85200872159308
